## City of Chicago API Capstone Project

## Imports

In [4]:
import pandas as pd
from sodapy import Socrata
from dotenv import load_dotenv
from os import getenv
import plotly.express as px
import scipy.stats as stats

## Retrieve City of Chicago Crimes - 2001 to Present API

In [5]:
load_dotenv() # dotenv is a seperate file to hide app_token, username, and password for security reasons
key = 'gaFHTdsEerkgHf8zQsgfx2JEC'
url = 'https://data.cityofchicago.org/resource/ijzp-q8t2.json' # URL to grab data
client = Socrata('data.cityofchicago.org', 
                 app_token=getenv('app_token'), # Inserts app token from hidden .env file
                 username=getenv('user_name'), # Inserts username from hidden .env file
                 password=getenv('password')) # Inserts password from hidden .env file

result = client.get('ijzp-q8t2', limit=15000) # Call to API with a limit of 15,000 data

result # Grab the results

[{'id': '13047842',
  'case_number': 'JG230250',
  'date': '2023-04-19T23:59:00.000',
  'block': '086XX S WALLACE ST',
  'iucr': '2826',
  'primary_type': 'OTHER OFFENSE',
  'description': 'HARASSMENT BY ELECTRONIC MEANS',
  'location_description': 'APARTMENT',
  'arrest': False,
  'domestic': False,
  'beat': '0622',
  'district': '006',
  'ward': '21',
  'community_area': '71',
  'fbi_code': '26',
  'x_coordinate': '1173810',
  'y_coordinate': '1847690',
  'year': '2023',
  'updated_on': '2023-04-26T16:53:52.000',
  'latitude': '41.737469673',
  'longitude': '-87.63879092',
  'location': {'latitude': '41.737469673',
   'longitude': '-87.63879092',
   'human_address': '{"address": "", "city": "", "state": "", "zip": ""}'},
  ':@computed_region_awaf_s7ux': '18',
  ':@computed_region_6mkv_f3dw': '21554',
  ':@computed_region_vrxf_vc4k': '70',
  ':@computed_region_bdys_3d7i': '529',
  ':@computed_region_43wa_7qmu': '13',
  ':@computed_region_rpca_8um6': '59',
  ':@computed_region_d9mm_jg

## Transfer data into pandas dataframe

In [30]:
df = pd.DataFrame.from_records(result)
display(df)

id case_number                     date  \
0      13047842    JG230250  2023-04-19T23:59:00.000   
1      13047863    JG230233  2023-04-19T23:58:00.000   
2      13047913    JG230238  2023-04-19T23:52:00.000   
3      13047803    JG230226  2023-04-19T23:49:00.000   
4      13047857    JG230259  2023-04-19T23:45:00.000   
...         ...         ...                      ...   
14995  13024273    JG202441  2023-03-28T15:20:00.000   
14996  13024218    JG202298  2023-03-28T15:15:00.000   
14997  13024485    JG202513  2023-03-28T15:15:00.000   
14998  13024317    JG202323  2023-03-28T15:14:00.000   
14999  13024719    JG202299  2023-03-28T15:10:00.000   

                          block  iucr       primary_type  \
0            086XX S WALLACE ST  2826      OTHER OFFENSE   
1            014XX W PRATT BLVD  0460            BATTERY   
2             079XX S ESSEX AVE  0486            BATTERY   
3            039XX S KEDZIE AVE  0326            ROBBERY   
4          067XX W DIVERSEY AVE  143A  WEAPONS VIOLATION   
...                         ...   ...                ...   
14995       002XX E ILLINOIS ST  1320    CRIMINAL DAMAGE   
14996         025XX W HIRSCH ST  0560            ASSAULT   
14997  070XX S STONY ISLAND AVE  0560            ASSAULT   
14998          054XX N CLARK ST  0860              THEFT   
14999         013XX W CORTEZ ST  0460            BATTERY   

                          description location_description  arrest  domestic  \
0      HARASSMENT BY ELECTRONIC MEANS            APARTMENT   False     False   
1                              SIMPLE    CONVENIENCE STORE    True     False   
2             DOMESTIC BATTERY SIMPLE            APARTMENT   False      True   
3      AGGRAVATED VEHICULAR HIJACKING          GAS STATION   False     False   
4       UNLAWFUL POSSESSION - HANDGUN               STREET    True     False   
...                               ...                  ...     ...       ...   
14995                      TO VEHICLE               STREET   False     False   
14996                          SIMPLE               STREET   False     False   
14997                          SIMPLE             SIDEWALK   False     False   
14998                    RETAIL THEFT           DRUG STORE   False     False   
14999                          SIMPLE            APARTMENT   False      True   

       ...      longitude                                           location  \
0      ...   -87.63879092  {'latitude': '41.737469673', 'longitude': '-87...   
1      ...  -87.666219555  {'latitude': '42.005446228', 'longitude': '-87...   
2      ...  -87.563796175  {'latitude': '41.751061918', 'longitude': '-87...   
3      ...  -87.704491075  {'latitude': '41.821345947', 'longitude': '-87...   
4      ...  -87.794791659  {'latitude': '41.930894401', 'longitude': '-87...   
...    ...            ...                                                ...   
14995  ...  -87.622476522  {'latitude': '41.890961404', 'longitude': '-87...   
14996  ...  -87.690154221  {'latitude': '41.906637573', 'longitude': '-87...   
14997  ...  -87.585941418  {'latitude': '41.766910975', 'longitude': '-87...   
14998  ...  -87.668375719  {'latitude': '41.981051896', 'longitude': '-87...   
14999  ...  -87.661190222  {'latitude': '41.9008021', 'longitude': '-87.6...   

      :@computed_region_awaf_s7ux :@computed_region_6mkv_f3dw  \
0                              18                       21554   
1                              46                       21853   
2                              43                       21202   
3                              49                       22248   
4                              39                        4454   
...                           ...                         ...   
14995                          22                       21182   
14996                          10                       21560   
14997                          32                       22538   
14998                          40              

Looking at the datatypes, there is a lot of cleaning that needs to be done
- Change column types
- Lower case values in columns
- Switch date to datetime?
- Delete unwanted columns
- Take care of NA values

## Drop Unwanted Columns

In [31]:
df = df.drop(columns=[':@computed_region_awaf_s7ux', ':@computed_region_6mkv_f3dw',
                 ':@computed_region_vrxf_vc4k', ':@computed_region_bdys_3d7i',
                 ':@computed_region_43wa_7qmu', ':@computed_region_rpca_8um6',
                 ':@computed_region_d9mm_jgwp', ':@computed_region_d3ds_rm58',
                 'ward', 'location'], axis=1)


## Lower case values in dataframe
- Used apply and lambda to check if the data type is an object, lower case the value

In [32]:
df = df.apply(lambda x: x.str.lower() if x.dtype == "object" else x) 
df

id case_number                     date  \
0      13047842    jg230250  2023-04-19t23:59:00.000   
1      13047863    jg230233  2023-04-19t23:58:00.000   
2      13047913    jg230238  2023-04-19t23:52:00.000   
3      13047803    jg230226  2023-04-19t23:49:00.000   
4      13047857    jg230259  2023-04-19t23:45:00.000   
...         ...         ...                      ...   
14995  13024273    jg202441  2023-03-28t15:20:00.000   
14996  13024218    jg202298  2023-03-28t15:15:00.000   
14997  13024485    jg202513  2023-03-28t15:15:00.000   
14998  13024317    jg202323  2023-03-28t15:14:00.000   
14999  13024719    jg202299  2023-03-28t15:10:00.000   

                          block  iucr       primary_type  \
0            086xx s wallace st  2826      other offense   
1            014xx w pratt blvd  0460            battery   
2             079xx s essex ave  0486            battery   
3            039xx s kedzie ave  0326            robbery   
4          067xx w diversey ave  143a  weapons violation   
...                         ...   ...                ...   
14995       002xx e illinois st  1320    criminal damage   
14996         025xx w hirsch st  0560            assault   
14997  070xx s stony island ave  0560            assault   
14998          054xx n clark st  0860              theft   
14999         013xx w cortez st  0460            battery   

                          description location_description  arrest  domestic  \
0      harassment by electronic means            apartment   False     False   
1                              simple    convenience store    True     False   
2             domestic battery simple            apartment   False      True   
3      aggravated vehicular hijacking          gas station   False     False   
4       unlawful possession - handgun               street    True     False   
...                               ...                  ...     ...       ...   
14995                      to vehicle               street   False     False   
14996                          simple               street   False     False   
14997                          simple             sidewalk   False     False   
14998                    retail theft           drug store   False     False   
14999                          simple            apartment   False      True   

       beat district community_area fbi_code x_coordinate y_coordinate  year  \
0      0622      006             71       26      1173810      1847690  2023   
1      2431      024              1      08b      1165565      1945281  2023   
2      0422      004             46      08b      1194234      1852817  2023   
3      0921      009             58       03      1155655      1878116  2023   
4      2511      025             18       15      1130791      1917868  2023   
...     ...      ...            ...      ...          ...          ...   ...   
14995  1834      018              8       14      1177800      1903658  2023   
14996  1423      014             24      08a      1159330      1909225  2023   
14997  0332      003             43      08a      1188141      1858539  2023   
14998  2012      020             77       06      1165048      1936387  2023   
14999  1213      012             24      08b      1167231      1907159  2023   

                    updated_on      latitude      longitude  
0      2023-04-26t16:53:52.000  41.737469673   -87.63879092  
1      2023-04-26t16:53:52.000  42.005446228  -87.666219555  
2      2023-04-26t16:53:52.000  41.751061918  -87.563796175  
3      2023-04-26t16:53:52.000  41.821345947  -87.704491075  
4      2023-04-26t16:53:52.000  41.930894401  -87.794791659  
...                        ...           ...            ...  
14995  2023-04-04t16:59:25.000  41.890961404  -87.622476522  
14996  2023-04-04t16:59:25.000  41.906637573  -87.690154221  
14997  2023-04-04t16:59:25.000  41.766910975  -87.585941418  
14998  2023-04-04t16:59:25.000  41.981051896  -87.668375719  
14999  2023-04-

## Change date and updated_on to datetime

In [20]:
df['date'] = pd.to_datetime(df['date'])
df['updated_on'] = pd.to_datetime(df['updated_on'])

## Data type conversions
- columns that were originally objects that need conversion to INT or FLOAT

In [40]:
df['id'] = df['id'].astype(int)
df['beat'] = df['beat'].astype(int)
df['district'] = df['district'].astype(int)
df['x_coordinate'] = df['x_coordinate'].astype(float)
df['y_coordinate'] = df['y_coordinate'].astype(float)
df['latitude'] = df['latitude'].astype(float)
df['longitude'] = df['longitude'].astype(float)
df['community_area'] = df['community_area'].astype(int)
df['year'] = df['year'].astype(int)

In [41]:
print(df.dtypes)
df['primary_type'].value_counts()

id                        int32
case_number              object
date                     object
block                    object
iucr                     object
primary_type             object
description              object
location_description     object
arrest                     bool
domestic                   bool
beat                      int32
district                  int32
community_area            int32
fbi_code                 object
x_coordinate            float64
y_coordinate            float64
year                      int32
updated_on               object
latitude                float64
longitude               float64
dtype: object


theft                                3081
battery                              2642
criminal damage                      1864
motor vehicle theft                  1826
assault                              1354
other offense                         892
deceptive practice                    828
weapons violation                     541
robbery                               538
burglary                              405
criminal trespass                     268
narcotics                             243
offense involving children            116
criminal sexual assault                84
sex offense                            78
public peace violation                 57
interference with public officer       48
homicide                               42
stalking                               25
arson                                  25
intimidation                           13
concealed carry license violation      11
liquor law violation                    8
prostitution                      

## View other offense to read description
- Once I have all rows of 'other offense' I can look at the description and add the keywords to my function to update the crime_rating column

In [142]:
df_test = df[df['primary_type'] == 'other offense']
df_test.tail(20)

id case_number                date                    block  \
14682  13024769    jg202871 2023-03-28 23:20:00      024xx w belmont ave   
14683  13024848    jg202913 2023-03-28 23:19:00      103xx s calhoun ave   
14713  13024800    jg202845 2023-03-28 22:15:00          006xx e 32nd st   
14715  13025052    jg203185 2023-03-28 22:12:00      092xx s brandon ave   
14733  13024686    jg202811 2023-03-28 21:55:00       027xx n cicero ave   
14735  13024806    jg202908 2023-03-28 21:44:00           005xx w oak st   
14746  13024673    jg202764 2023-03-28 21:07:00     006xx n parkside ave   
14747  13024669    jg202762 2023-03-28 21:04:00   032xx n nottingham ave   
14780  13026233    jg204327 2023-03-28 20:30:00          012xx e 64th st   
14786  13024723    jg202736 2023-03-28 20:01:00         0000x w 112th pl   
14798  13024761    jg202839 2023-03-28 20:00:00      029xx n western ave   
14809  13025654    jg203968 2023-03-28 19:38:00  032xx w washington blvd   
14827  13024474    jg202644 2023-03-28 19:15:00        013xx s throop st   
14842  13024447    jg202622 2023-03-28 18:59:00    053xx w fullerton ave   
14892  13024341    jg202521 2023-03-28 17:30:00      019xx s harding ave   
14948  13025590    jg203818 2023-03-28 16:02:00       043xx w gladys ave   
14955  13024295    jg202436 2023-03-28 16:00:00    084xx s ingleside ave   
14966  13027429    jg206007 2023-03-28 16:00:00   079xx s sacramento ave   
14988  13024327    jg202530 2023-03-28 15:30:00          024xx w 34th pl   
14994  13028674    jg207633 2023-03-28 15:20:00      048xx n central ave   

       iucr   primary_type                           description  \
14682  4389  other offense       violation gps monitoring device   
14683  501a  other offense                animal abuse / neglect   
14713  4387  other offense           violate order of protection   
14715  2820  other offense                      telephone threat   
14733  502p  other offense          false / stolen / altered trp   
14735  4387  other offense           violate order of protection   
14746  2820  other offense                      telephone threat   
14747  502r  other offense  vehicle title / registration offense   
14780  2820  other offense                      telephone threat   
14786  2825  other offense               harassment by telephone   
14798  2820  other offense                      telephone threat   
14809  2825  other offense               harassment by telephone   
14827  2820  other offense                      telephone threat   
14842  502p  other offense          false / stolen / altered trp   
14892  2825  other offense               harassment by telephone   
14948  2825  other offense               harassment by telephone   
14955  2825  other offense               harassment by telephone   
14966  2826  other offense        harassment by electronic means   
14988  2820  other offense                      telephone threat   
14994  2826  other offense        harassment by electronic means   

                        location_description  arrest  domestic  beat  \
14682  police facility / vehicle parking lot   False     False  1921   
14683                              residence   False     False   434   
14713                              apartment   False      True   211   
14715                              apartment   False      True   424   
14733                                 street    True     False  2521   
14735                              apartment    True      True  1823   
14746                              apartment   False     False  1511   
14747                                 street    True     False  1632   
14780                                 street   False      True   314   
14786                              residence   False      True   522   
14798                              apartment   False     False  1432   
14809                              apartment   False     False  1123   
14827                              residence   Fals

## Create function to create a crime rating column based on the severity of the crimes

In [45]:
def func(df):
    if df['primary_type'] == 'battery':
        return 5
    elif df['primary_type'] == 'criminal damage':
        return 5
    elif df['primary_type'] == 'assault':
        return 5
    elif df['primary_type'] == 'narcotics':
        return 5
    elif df['primary_type'] == 'offense involving children':
        return 5
    elif df['primary_type'] == 'criminal sexual assault':
        return 5
    elif df['primary_type'] == 'sex offense':
        return 5
    elif df['primary_type'] == 'homicide':
        return 5
    elif df['primary_type'] == 'arson':
        return 5
    elif df['primary_type'] == 'kidnapping':
        return 5
    elif df['primary_type'] == 'theft':
        return 4
    elif df['primary_type'] == 'motor vehicle theft':
        return 4
    elif df['primary_type'] == 'deceptive practice':
        return 4
    elif df['primary_type'] == 'criminal trespass':
        return 4
    elif df['primary_type'] == 'prostitution':
        return 4
    elif df['primary_type'] == 'robbery':
        return 4
    elif df['primary_type'] == 'burglary':
        return 4
    elif df['primary_type'] == 'weapons violation':
        return 3
    elif df['primary_type'] == 'interference with public officer':
        return 3
    elif df['primary_type'] == 'stalking':
        return 3
    elif df['primary_type'] == 'public peace violation':
        return 2
    elif df['primary_type'] == 'obscenity':
        return 2
    elif df['primary_type'] == 'intimidation':
        return 1
    elif df['primary_type'] == 'liquor law violation':
        return 1
    elif df['primary_type'] == 'concealed carry license violation':
        return 1
      

df['crime_rating'] = df.apply(func, axis=1)

In [42]:
def crime_rat(primary_type):
    key5 = ['battery', 'criminal damage', 'assault', 'narcotics', 'offense', 'criminal', 'sex', 'homicide', 'arson', 'kidnapping', 'weapons', 'criminal', 'concealed'] # Keywords to look for to return 5
    key4 = ['theft', 'motor vehicle theft', 'deceptive practice', 'criminal trespass', 'prostitution', 'robbery', 'burglary', 'deceptive', 'violate'] # Keywords to look for to return 4
    key3 = ['weapons violation', 'interference with public officer', 'stalking', 'interference', 'violation'] # Keywords to look for to return 3
    key2 = ['public', 'obscenity', 'peace'] # Keywords to look for to return 2
    key1 = ['intimidation', 'liquor', 'concealed'] # Keywords to look for to return 1
    for word in primary_type.split(): # Iterate through column 'primary_type' to find word that is inside my keyword lists above
        if word in key5:
            return 5
        elif word in key4:
            return 4
        elif word in key3:
            return 3
        elif word in key2:
            return 2
        elif word in key1:
            return 1
        
df['crime_rating'] = df['primary_type'].apply(crime_rat) # create crime_rating column -> search 'primary_type' and apply the crime_rat function above

In [43]:
sorted(df['crime_rating'].unique())

[1, 2, 3, 4, 5]

## Create function for crime description 'other offense'
- Read into the description to find the severity of the crime and update the crime_rating column based on description

In [44]:
def fix_rating(description):
    key2 = ['license'] # Keyword to look for to return 2
    key3 = ['harassment', 'telephone', 'vehicle'] # Keywords to look for to return 3
    key4 = ['violate', 'other', 'false', 'gun', 'violation'] # Keywords to look for to return 4
    key5 = ['animal', 'sex', 'money', 'board', 'violent', 'abuse'] # Keywords to look for to return 5
    for word in description.split(): # iterate through description to find if word is inside any of the lists above
        if word in key2:
            return 2 # returns the value I specify
        elif word in key3:
            return 3
        elif word in key4:
            return 4
        elif word in key5:
            return 5
# apply fix_rating function to columns in df where primary_type is equal to other_offense. fix_rating is updating crime_rating column where the primary_type is other offense
df.loc[df['primary_type'] == 'other offense', 'crime_rating'] = df.loc[df['primary_type'] == 'other offense', 'description'].apply(lambda x: fix_rating(x)) 


## Visualization

In [45]:
fig = px.scatter_mapbox(df, lat='latitude', lon='longitude', color='community_area', hover_data=['primary_type', 'arrest'],
                        zoom=10, height=500)

fig.update_layout(mapbox_style = 'open-street-map')
fig.show()

In [46]:
fig2 = px.scatter_mapbox(df, lat='latitude', lon='longitude', color='district', hover_data=['primary_type', 'arrest'],
                        zoom=10, height=500)

fig2.update_layout(mapbox_style = 'open-street-map')
fig2.show()

In [47]:
fig1 = px.scatter_mapbox(df, lat='latitude', lon='longitude', color='crime_rating', hover_data=['primary_type', 'arrest'],
                        zoom=10, height=500)

fig1.update_layout(mapbox_style = 'open-street-map')
fig1.show()

## nullHypothesis - No relation between crime rates and districts

## altHypothesis - Low districts will have higher crime rates

In [148]:
# Filter df to get districts equal to the value I chose

df7 = df[df['district'] == 7]
df24 = df[df['district'] == 24]

df6 = df[df['district'] == 6]
df14 = df[df['district'] == 14]


## Get mean and std of filtered data

In [149]:
mean_df7 = df7['crime_rating'].mean()
std_df7 = df7['crime_rating'].std()

mean_df24 = df24['crime_rating'].mean()
std_df24 = df24['crime_rating'].std()

print(mean_df7)
print(mean_df24)
print('\n')
print(std_df7)
print(std_df24)

4.569940476190476
4.314031180400891


0.5709207633824275
0.6209181054442442


In [150]:
mean_df6 = df6['crime_rating'].mean()
std_df6 = df6['crime_rating'].std()

mean_df14 = df14['crime_rating'].mean()
std_df14 = df14['crime_rating'].std()

print(mean_df6)
print(mean_df14)
print('\n')
print(std_df6)
print(std_df14)

4.5291529152915295
4.338870431893688


0.5922382019294614
0.5635495302406189


## Chi-Squared Test

Using pd.crosstab to compute a contingency table of two or more factors. 
Grab one or more columns as input



Returns the counts of each combination as input factors.

In [151]:
# create contingency table
type_district_table = pd.crosstab(df['primary_type'], df['district'])

# chi-squared test, p-value, degree of freedom, expected frequencies
chi2_stat, p_val, dof, expected = stats.chi2_contingency(type_district_table)

# print results. :.2f and :.4 represents float numbers with 2 and 4 decimal places
print("Chi-square statistic: {:.2f}, p-value: {:.4f}".format(chi2_stat, p_val))


Chi-square statistic: 2325.80, p-value: 0.0000


In [152]:
# contingency table of district and crime rating
dist_crime_table = pd.crosstab(df['district'], df['crime_rating'])

# chi-square test of independence
chi2_stat, p_val, dof, expected = stats.chi2_contingency(dist_crime_table)

print("Chi-square statistic: {:.2f}, p-value: {:.4f}".format(chi2_stat, p_val))


Chi-square statistic: 627.86, p-value: 0.0000


In [153]:
fig = px.bar(type_district_table, x=type_district_table.index, y=type_district_table.columns,
             title='Number of Crimes by District and Primary Type',
             labels={'x': 'District', 'y': 'Number of Crimes'},
             barmode='relative')
fig.show()

In [154]:
df7 = df[df['district'] == 7] # Filters district column of dataframe to display district 7
df24 = df[df['district'] == 24] # Filters district column of dataframe to display district 24

# Display df7 by primary type and crime rating, color coded by crime rating
fig3 = px.bar(df7, x='primary_type', y='crime_rating', color='crime_rating',
            color_continuous_scale=px.colors.sequential.Reds, # Color scheme
            title='District 7 Crime Count', hover_data=['primary_type']) # Data shown when hovering over chart
fig3.show() # .show() to display the bar chart

# Display df24 by primary type and crime rating, color coded by crime rating
fig4 = px.bar(df24, x='primary_type', y='crime_rating', color='crime_rating',
            color_continuous_scale=px.colors.sequential.Darkmint, # Color scheme 
            title='District 24 Crime Count')
fig4.show() # .show() to display the bar chart

### These graphs show high crime rating crimes but vary in the types. District 24, which is a higher income area has a higher theft count than lower income districts like district 7. District 7 shows more battery and assault crimes compared to district 24.

In [58]:
df6 = df[df['district'] == 6]
df14 = df[df['district'] == 14]

fig3 = px.bar(df6, x='primary_type', y='crime_rating', color='crime_rating',  color_continuous_scale=px.colors.sequential.Reds, title='District 6 Crime Count', hover_data=['primary_type'])
fig3.show()

fig4 = px.bar(df14, x='primary_type', y='crime_rating', color='crime_rating', color_continuous_scale=px.colors.sequential.Darkmint, title='District 14 Crime Count')
fig4.show()

In [48]:
df.to_csv('crimecapstone.csv', index=False)
